# Poro34B Lora fine-tuning with S-Group's data - 1 Q/A

In [ ]:
# This script finetunes the Poro34B model with 1 Question and Answer pair

## Initialization

In [ ]:
# pip install peft, all other Python libraries are already in AWS image
!pip install peft

In [2]:
import torch
import json
from transformers import AutoModelForCausalLM, AutoTokenizer 
from transformers import TrainingArguments, Trainer
from transformers import pipeline
from peft import  get_peft_model, PromptTuningConfig, TaskType, PromptTuningInit
from datasets import load_dataset

2024-02-29 15:06:36.945989: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: SSE4.1 SSE4.2 AVX AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [3]:
# this checks wether we have GPU
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")

In [4]:
print(device)

cpu


## Foundation model import

In [5]:
# Foundation model
model_name='LumiOpen/Poro-34B'

In [6]:
tokenizer = AutoTokenizer.from_pretrained(model_name)

In [7]:
branch = "1000B"
model = AutoModelForCausalLM.from_pretrained(model_name,
    torch_dtype=torch.bfloat16,
    revision=branch,
)

Loading checkpoint shards:   0%|          | 0/14 [00:00<?, ?it/s]

## Setting up the Lora parameters

In [1]:
from peft import LoraConfig, get_peft_model

2024-02-29 15:28:54.008508: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: SSE4.1 SSE4.2 AVX AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [38]:
config = LoraConfig(
    r=8,
    lora_alpha=8,
    target_modules=["query_key_value"],
    lora_dropout=0.05,
    bias="none",
    task_type="CAUSAL_LM"
)

In [39]:
peft_model = get_peft_model(model, config)

In [40]:
trainable_params = 0
all_param = 0

# iterating over all parameters
for _, param in peft_model.named_parameters():
    # adding parameters to total
    all_param += param.numel()
    # adding parameters to trainable if they require a graident
    if param.requires_grad:
        trainable_params += param.numel()

# print number of trainable parameters
print(f"trainable params: {trainable_params}")
print(f"all params: {all_param}")
print(f"trainable: {100 * trainable_params / all_param:.2f}%")

trainable params: 12386304
all params: 34229336064
trainable: 0.04%


## Preparing the training data

In [10]:
# prepare the data for training
def prepare_train_data(data):
    text_input = data['text']
    tokenized_input = tokenizer(text_input, return_tensors='pt', padding=True)
    tokenized_input['labels'] = tokenized_input['input_ids']
    return tokenized_input

In [41]:
dataset = load_dataset("json", data_files="prompts_1.json")

In [42]:
train_dataset = dataset['train'].map(prepare_train_data, batched=True, remove_columns=["text"])

## Setting up the training parameters

In [50]:
from transformers import DataCollatorForLanguageModeling

In [53]:
trainer = Trainer(
    model=peft_model,
    train_dataset=train_dataset,
    args=TrainingArguments(
        per_device_train_batch_size=4,
        gradient_accumulation_steps=4,
        warmup_steps=20,
        max_steps=20,
        learning_rate=1e-3,
        logging_steps=1,
        output_dir='outputs',
    ),
    data_collator=DataCollatorForLanguageModeling(tokenizer, mlm=False)
)

In [54]:
trainer.train()

TrainOutput(global_step=20, training_loss=0.428607177734375, metrics={'train_runtime': 1747.2099, 'train_samples_per_second': 0.183, 'train_steps_per_second': 0.011, 'total_flos': 219858091622400.0, 'train_loss': 0.428607177734375, 'epoch': 20.0})

## Saving the finetuned model

In [13]:
model_id = "Poro-34B-Lora-1"

In [ ]:
peft_model.save_pretrained(model_id)

In [ ]:
!ls -lh {model_id}  # Lora parameters file size

## Testing

In [8]:
def generate_output(model, inputs, max_new_tokens=100):
    outputs = model.generate(
        input_ids=inputs["input_ids"],
        max_new_tokens=max_new_tokens,
        temperature=0.1,
    )
    return outputs

### Original model

In [9]:
prompt = tokenizer('Given the question delimited by triple backticks ```{ Kuinka vaihdan uutiskirjeen sähköpostiosoitteen? }```, what is the answer? Answer:', return_tensors="pt")
result = generate_output(model,prompt)
print(tokenizer.batch_decode(result, skip_special_tokens=True))

['Given the question delimited by triple backticks ```{ Kuinka vaihdan uutiskirjeen sähköpostiosoitteen? }```, what is the answer? Answer: ```{ Voit vaihtaa uutiskirjeen sähköpostiosoitteen kirjautumalla sisään ja menemällä Oma tili -osioon. }```\n']


### Finetuned model

In [11]:
from peft import PeftModel

In [14]:
loaded_model = PeftModel.from_pretrained(model,model_id,is_trainable=False)

In [15]:
prompt = tokenizer('Given the question delimited by triple backticks ```{ Kuinka vaihdan uutiskirjeen sähköpostiosoitteen? }```, what is the answer? Answer:', return_tensors="pt")
result = generate_output(loaded_model,prompt)
print(tokenizer.batch_decode(result, skip_special_tokens=True))

['Given the question delimited by triple backticks ```{ Kuinka vaihdan uutiskirjeen sähköpostiosoitteen? }```, what is the answer? Answer: { Peruuta ensin vanhaan osoitteeseen tilattu uutiskirje kirjeen alareunan “Peruuta tilaus” -linkistä.\nTilaa uutiskirje uudelleen oikeaan osoitteeseen. }.\nKuinka vaihdan uutiskirjeen sähköpostiosoitteen?\nPeruuta ensin vanhaan osoitteeseen tilattu uutiskirje kirjeen alareunan “Peruuta tilaus” -linkistä.\nTilaa uutiskirje uudelleen oikeaan osoitteeseen.\nPeruuta uutiskirjeen tilaus kirjeen alareunan “Peruuta tilaus” -linkistä.\nTilaa uutiskirje uudelleen oikeaan osoitteeseen.\nPeruuta uutiskirjeen tilaus kirjeen alareunan “Peruuta tilaus” -linkistä.\nTilaa uutiskirje']
